<h1 align=center><font size = 5>IBM Data science Proffessional Certificate: Battle of the Neighborhoods in New York City</font></h1>

## Introduction

In this Notebook,we analyse newyork neibourhoods . Also, will use the Foursquare API to explore neighborhoods in New York City. Additionaly   will also use the **explore** function to get the most common venue categories in each neighborhood, and then use this feature to group the neighborhoods into clusters. Then use the *k*-means clustering algorithm to complete this task. Finally, will use the Folium library to visualize the neighborhoods in New York City and their emerging clusters.

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in New York City</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

## 1. Downloading and Exploring the Dataset

Best on the data used in this study, the New york Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood. 

This dataset exists for free on the web. Feel free to try to find this dataset on your own, but here is the link to the dataset: https://geo.nyu.edu/catalog/nyu_2451_34572

In [4]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


#### Load and explore the data

now let load the data

In [5]:
import json
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

we then take a quick look at our data

In [6]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

Notice how all the relevant data is in the features key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [7]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.

In [8]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a *pandas* dataframe
Tranform the data into a pandas dataframe The next task is essentially transforming this data of nested Python dictionaries into a pandas dataframe. So let's start by creating an empty dataframe.

In [9]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [10]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [11]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [12]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods

In [13]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.

In [14]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [15]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork


**Folium is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.**



**Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.**

In [16]:
CLIENT_ID = 'XDSVHHZ0OH2OITHZSB5MJSEHSUVR5J3CYY5EOHOQTV550IQ1' # your Foursquare ID
CLIENT_SECRET = '5MNXPTBQ4GVTH0KMT0H0UKX00KYCEDLTI0XLT5BKJGME4AO3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: XDSVHHZ0OH2OITHZSB5MJSEHSUVR5J3CYY5EOHOQTV550IQ1
CLIENT_SECRET:5MNXPTBQ4GVTH0KMT0H0UKX00KYCEDLTI0XLT5BKJGME4AO3


**Let's explore the first neighborhood in our dataframe.**

lets get the neighbourhood name

In [17]:
neighborhoods.loc[0, 'Neighborhood']

'Wakefield'

**Get neignborhoods by value**

lets get the coordinates of the neibourghood

In [18]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


#### Now, let's get the top 100 venues that are in Wakefield within a radius of 500 meters.

In [19]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL


'https://api.foursquare.com/v2/venues/explore?&client_id=XDSVHHZ0OH2OITHZSB5MJSEHSUVR5J3CYY5EOHOQTV550IQ1&client_secret=5MNXPTBQ4GVTH0KMT0H0UKX00KYCEDLTI0XLT5BKJGME4AO3&v=20180605&ll=40.89470517661,-73.84720052054902&radius=500&limit=100'

Send the GET request and examine the resutls

In [20]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e08dddf60ba08001bf98633'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Wakefield',
  'headerFullLocation': 'Wakefield, Bronx',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 8,
  'suggestedBounds': {'ne': {'lat': 40.899205181110005,
    'lng': -73.84125857127495},
   'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c537892fd2ea593cb077a28',
       'name': 'Lollipops Gelato',
       'location': {'address': '4120 Baychester Ave',
        'crossStreet': 'Edenwald & Bussing Ave',
        'lat': 40.894123150205274,
        'lng': -73.84589162362325,
        'labeledLatLn

In [21]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a pandas dataframe.

In [22]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat        lng
0  Lollipops Gelato    Dessert Shop  40.894123 -73.845892
1          Rite Aid        Pharmacy  40.896649 -73.844846
2  Carvel Ice Cream  Ice Cream Shop  40.890487 -73.848568
3             Shell     Gas Station  40.894187 -73.845862
4           Dunkin'      Donut Shop  40.890459 -73.849089

And how many venues were returned by Foursquare?

In [23]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

8 venues were returned by Foursquare.


Explore Neighborhoods in newyork

##  Explore Neighborhoods in newyork

## Let's create a function to repeat the same process to all the neighborhoods in New york

In [24]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *New york_venues*.

In [26]:
# type your answer here

newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

**Now Let's check the size of the resulting dataframe**

In [27]:
print(newyork_venues.shape)
newyork_venues.head()

(10288, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3             Shell       40.894187       -73.845862     Gas Station  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [28]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      29                      29   
Annadale                                      13                      13   
Arden Heights                                  5                       5   
Arlington                                      4                       4   
Arrochar                                      20                      20   
Arverne                                       18                      18   
Astoria                                      100                     100   
Astoria Heights                               13                      13   
Auburndale                                    18                      18   
Bath Beach                                    48                      48   
Battery Park City                             93                      93   
Bay Ridge                                     85                      85   
Bay Terrace                                   47                      47   
Baychester                                    22                      22   
Bayside                                       73                      73   
Bayswater                                      2                       2   
Bedford Park                                  34                      34   
Bedford Stuyvesant                            25                      25   
Beechhurst                                    15                      15   
Bellaire                                      12                      12   
Belle Harbor                                  17                      17   
Bellerose                                     22                      22   
Belmont                                       98                      98   
Bensonhurst                                   28                      28   
Bergen Beach                                   6                       6   
Blissville                                    19                      19   
Bloomfield                                     5                       5   
Boerum Hill                                   91                      91   
Borough Park                                  24                      24   
Breezy Point                                   5                       5   
Briarwood                                      8                       8   
Brighton Beach                                45                      45   
Broad Channel                                  5                       5   
Broadway Junction                             14                      14   
Bronxdale                                     12                      12   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   23                      23   
Bulls Head                                    40                      40   
Bushwick                                      75                      75   
Butler Manor                                   6                       6   
Cambria Heights                               11                      11   
Canarsie                                       5                       5   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                    9                       9   
Castleton Corners                             14                      14   
Central Harlem                                43                      43   
Charleston                                    31                      31   
Chelsea                                      108                     108   
Chinatown                                    100                     100   

In [29]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 429 uniques categories.


In [30]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.tail()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
10283            0                  0               0                  0   
10284            0                  0               0                  0   
10285            0                  0               0                  0   
10286            0                  0               0                  0   
10287            0                  0               0                  0   

       African Restaurant  Airport Terminal  American Restaurant  \
10283                   0                 0                    0   
10284                   0                 0                    0   
10285                   0                 0                    0   
10286                   0                 0                    0   
10287                   0                 0                    0   

       Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
10283             0       0                 0                       0   
10284             0       0                 0                       0   
10285             0       0                 0                       0   
10286             0       0                 0                       0   
10287             0       0                 0                       0   

       Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
10283            0           0                    0                     0   
10284            0           0                    0                     0   
10285            0           0                    0                     0   
10286            0           0                    0                     0   
10287            0           0                    0                     0   

       Asian Restaurant  Athletics & Sports  Auditorium  \
10283                 0                   0           0   
10284                 0                   0           0   
10285                 0                   0           0   
10286                 0                   0           0   
10287                 0                   0           0   

       Australian Restaurant  Austrian Restaurant  Auto Garage  \
10283                      0                    0            0   
10284                      0                    0            0   
10285                      0                    0            0   
10286                      0                    0            0   
10287                      0                    0            0   

       Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
10283                0          0           0           0       0     0    0   
10284                0          0           0           0       0     0    0   
10285                0          0           0           0       0     0    0   
10286                0          0           0           0       0     0    1   
10287                0          0           0           0       0     0    0   

       Baseball Field  Baseball Stadium  Basketball Court  Bath House  Beach  \
10283               0                 0                 0           0      0   
10284               0                 0                 0           0      0   
10285               0                 0                 0           0      0   
10286               0                 0                 0           0      0   
10287               0                 0                 0           0      0   

       Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
10283          0                0         0            0           0   
10284          0                0         0            0           0   
10285          0                0         0            0           0   
10286          0                0         0            0           0   
10287          0                0         0            0           0   

       Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
10283      

In [31]:
newyork_onehot.shape

(10288, 429)

In [32]:
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.021277   
13                  Baychester     0.000000           0.045455   
14                     Bayside     0.013699           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.021978           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030000           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.000000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.032609           0.000000   
59                  Co-op City     0.000000           0.00

**Let's confirm the new size**

In [33]:
newyork_grouped.shape

(300, 429)

**Let's print each neighborhood along with the top 5 most common venues**

In [35]:
num_top_venues = 5

for hood in newyork_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Pizza Place  0.14
1         Supermarket  0.10
2         Bus Station  0.07
3       Deli / Bodega  0.07
4  Spanish Restaurant  0.07


----Annadale----
           venue  freq
0    Pizza Place  0.23
1         Bakery  0.15
2          Diner  0.08
3           Park  0.08
4  Train Station  0.08


----Arden Heights----
           venue  freq
0       Pharmacy   0.2
1  Deli / Bodega   0.2
2    Coffee Shop   0.2
3       Bus Stop   0.2
4    Pizza Place   0.2


----Arlington----
               venue  freq
0      Grocery Store  0.25
1      Deli / Bodega  0.25
2         Playground  0.25
3     Scenic Lookout  0.25
4  Paella Restaurant  0.00


----Arrochar----
                venue  freq
0       Deli / Bodega  0.10
1  Italian Restaurant  0.10
2            Bus Stop  0.10
3      Cosmetics Shop  0.05
4   Polish Restaurant  0.05


----Arverne----
            venue  freq
0       Surf Spot  0.22
1  Sandwich Place  0.11
2   Metro Station  0.11
3        Bus 

                venue  freq
0  Italian Restaurant  0.11
1         Pizza Place  0.05
2         Coffee Shop  0.05
3              Bakery  0.04
4        Cocktail Bar  0.04


----Castle Hill----
            venue  freq
0  Baseball Field  0.11
1           Diner  0.11
2            Bank  0.11
3     Pizza Place  0.11
4          Market  0.11


----Castleton Corners----
               venue  freq
0        Pizza Place  0.21
1      Grocery Store  0.07
2  Indian Restaurant  0.07
3    Thai Restaurant  0.07
4               Bank  0.07


----Central Harlem----
                 venue  freq
0                  Bar  0.05
1   Seafood Restaurant  0.05
2       Cosmetics Shop  0.05
3   African Restaurant  0.05
4  American Restaurant  0.05


----Charleston----
                        venue  freq
0               Big Box Store  0.06
1              Cosmetics Shop  0.06
2               Women's Store  0.03
3                 Music Venue  0.03
4  Construction & Landscaping  0.03


----Chelsea----
                venue 

----Edgewater Park----
                venue  freq
0  Italian Restaurant  0.19
1          Donut Shop  0.10
2       Deli / Bodega  0.10
3         Pizza Place  0.10
4          Sports Bar  0.05


----Egbertville----
                        venue  freq
0              Clothing Store   0.2
1          Italian Restaurant   0.2
2                  Bagel Shop   0.2
3              Cosmetics Shop   0.2
4  Construction & Landscaping   0.2


----Elm Park----
                 venue  freq
0        Deli / Bodega  0.22
1             Bus Stop  0.22
2       Ice Cream Shop  0.11
3  American Restaurant  0.11
4   Italian Restaurant  0.11


----Elmhurst----
                       venue  freq
0            Thai Restaurant  0.21
1         Mexican Restaurant  0.12
2  South American Restaurant  0.09
3         Chinese Restaurant  0.06
4      Vietnamese Restaurant  0.06


----Eltingville----
                  venue  freq
0           Pizza Place  0.11
1      Sushi Restaurant  0.11
2                 Diner  0.06
3  Fast

               venue  freq
0        Supermarket  0.25
1  Mobile Phone Shop  0.25
2         Playground  0.25
3         Donut Shop  0.25
4           Pharmacy  0.00


----Homecrest----
                venue  freq
0                Bank  0.10
1          Donut Shop  0.08
2      Sandwich Place  0.08
3       Grocery Store  0.05
4  Chinese Restaurant  0.05


----Howard Beach----
                  venue  freq
0    Italian Restaurant  0.10
1              Pharmacy  0.05
2            Bagel Shop  0.05
3        Sandwich Place  0.05
4  Fast Food Restaurant  0.05


----Hudson Yards----
                  venue  freq
0   American Restaurant  0.06
1  Gym / Fitness Center  0.05
2                 Hotel  0.05
3                  Café  0.05
4    Italian Restaurant  0.05


----Huguenot----
                venue  freq
0                Bank  0.22
1       Deli / Bodega  0.11
2  Italian Restaurant  0.11
3      Ice Cream Shop  0.11
4      Sandwich Place  0.11


----Hunters Point----
                 venue  freq
0   

                 venue  freq
0   Chinese Restaurant  0.11
1  Japanese Restaurant  0.08
2          Pizza Place  0.08
3                 Bank  0.05
4       Cosmetics Shop  0.05


----Mill Island----
         venue  freq
0         Pool   1.0
1  Yoga Studio   0.0
2    Pet Store   0.0
3  Pet Service   0.0
4     Pet Café   0.0


----Morningside Heights----
                 venue  freq
0                 Park  0.10
1          Coffee Shop  0.07
2  American Restaurant  0.07
3            Bookstore  0.07
4       Sandwich Place  0.05


----Morris Heights----
                       venue  freq
0                IT Services  0.11
1  Latin American Restaurant  0.11
2                       Bank  0.11
3                Pizza Place  0.11
4              Grocery Store  0.11


----Morris Park----
            venue  freq
0     Pizza Place  0.19
1    Burger Joint  0.10
2   Deli / Bodega  0.10
3          Bakery  0.10
4  Sandwich Place  0.05


----Morrisania----
                  venue  freq
0        Discount Stor

                  venue  freq
0  Caribbean Restaurant  0.08
1           Pizza Place  0.06
2         Grocery Store  0.06
3  Fast Food Restaurant  0.06
4              Pharmacy  0.06


----Queens Village----
                venue  freq
0                Bank  0.14
1    Department Store  0.07
2          Donut Shop  0.07
3  Mexican Restaurant  0.07
4              Bakery  0.07


----Queensboro Hill----
                           venue  freq
0             Chinese Restaurant  0.12
1                           Bank  0.08
2                         Bakery  0.08
3                    Supermarket  0.04
4  Vegetarian / Vegan Restaurant  0.04


----Queensbridge----
              venue  freq
0             Hotel  0.19
1    Scenic Lookout  0.06
2    Sandwich Place  0.06
3  Basketball Court  0.06
4    Baseball Field  0.06


----Randall Manor----
           venue  freq
0       Bus Stop   0.4
1  Deli / Bodega   0.2
2     Bagel Shop   0.2
3           Park   0.2
4    Yoga Studio   0.0


----Ravenswood----
     

                venue  freq
0         Pizza Place  0.11
1  Italian Restaurant  0.07
2      Discount Store  0.04
3             Theater  0.04
4               Hotel  0.04


----Sunnyside Gardens----
           venue  freq
0            Bar  0.07
1  Grocery Store  0.06
2    Pizza Place  0.04
3    Coffee Shop  0.03
4       Pharmacy  0.03


----Sunset Park----
                       venue  freq
0                     Bakery  0.09
1                       Bank  0.09
2         Mexican Restaurant  0.09
3                Pizza Place  0.09
4  Latin American Restaurant  0.09


----Sutton Place----
                    venue  freq
0    Gym / Fitness Center  0.06
1      Italian Restaurant  0.05
2  Furniture / Home Store  0.04
3                     Gym  0.03
4       Indian Restaurant  0.03


----Throgs Neck----
                venue  freq
0       Deli / Bodega   0.2
1         Coffee Shop   0.1
2  Italian Restaurant   0.1
3    Asian Restaurant   0.1
4         Pizza Place   0.1


----Todt Hill----
         

**Let's put that into a *pandas* dataframe**

In [36]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

**Now let's create the new dataframe and display the top 10 venues for each neighborhood.**

In [90]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place           Supermarket   
1       Annadale           Pizza Place                Bakery   
2  Arden Heights              Pharmacy         Deli / Bodega   
3      Arlington         Deli / Bodega         Grocery Store   
4       Arrochar    Italian Restaurant         Deli / Bodega   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Chinese Restaurant         Deli / Bodega           Bus Station   
1                  Park                 Diner                   Pub   
2              Bus Stop           Coffee Shop           Pizza Place   
3        Scenic Lookout            Playground         Women's Store   
4              Bus Stop            Food Truck           Supermarket   

       6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0         Spanish Restaurant        Breakfast Spot      Martial Arts Dojo   
1              Train Station   American Restaurant             Restaurant   
2              Women's Store   Filipino Restaurant            Event Space   
3                      Field         Event Service            Event Space   
4  Middle Eastern Restaurant          Liquor Store  Outdoors & Recreation   

  9th Most Common Venue 10th Most Common Venue  
0  Fast Food Restaurant               Pharmacy  
1            Sports Bar       Sushi Restaurant  
2               Exhibit                Factory  
3               Exhibit                Factory  
4            Bagel Shop         Sandwich Place

## Now its time to Cluster Neighborhoods

We Run *k*-means to cluster the neighborhood into 5 clusters.

In [91]:
# set number of clusters
kclusters = 5

newyork_grouped_clustering = newyork_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 0, 0, 1, 1, 1, 1, 1, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [92]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = neighborhoods

# merge newyork_grouped with toronto_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

newyork_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             1.0   
1   Bronx   Co-op City  40.874294 -73.829939             1.0   
2   Bronx  Eastchester  40.887556 -73.827806             1.0   
3   Bronx    Fieldston  40.895437 -73.905643             1.0   
4   Bronx    Riverdale  40.890834 -73.912585             1.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0          Dessert Shop              Pharmacy            Donut Shop   
1           Bus Station        Baseball Field        Discount Store   
2  Caribbean Restaurant         Deli / Bodega           Bus Station   
3                 Plaza                 River           Bus Station   
4                  Park           Bus Station            Playground   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Laundromat           Gas Station        Sandwich Place   
1    Chinese Restaurant                  Park              Pharmacy   
2                 Diner         Bowling Alley         Metro Station   
3         Women's Store         Event Service           Event Space   
4                 Plaza                  Bank                   Gym   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Ice Cream Shop  Caribbean Restaurant                  Farm   
1            Bagel Shop         Grocery Store  Fast Food Restaurant   
2    Chinese Restaurant                Bakery  Fast Food Restaurant   
3               Exhibit               Factory    Falafel Restaurant   
4          Home Service        Baseball Field            Food Truck   

  10th Most Common Venue  
0   Fast Food Restaurant  
1              Gift Shop  
2     Seafood Restaurant  
3                   Farm  
4            Flower Shop

In [93]:
newyork_merged.isnull()

Borough  Neighborhood  Latitude  Longitude  Cluster Labels  \
0      False         False     False      False           False   
1      False         False     False      False           False   
2      False         False     False      False           False   
3      False         False     False      False           False   
4      False         False     False      False           False   
5      False         False     False      False           False   
6      False         False     False      False           False   
7      False         False     False      False           False   
8      False         False     False      False           False   
9      False         False     False      False           False   
10     False         False     False      False           False   
11     False         False     False      False           False   
12     False         False     False      False           False   
13     False         False     False      False           False   
14     False         False     False      False           False   
15     False         False     False      False           False   
16     False         False     False      False           False   
17     False         False     False      False           False   
18     False         False     False      False           False   
19     False         False     False      False           False   
20     False         False     False      False           False   
21     False         False     False      False           False   
22     False         False     False      False           False   
23     False         False     False      False           False   
24     False         False     False      False           False   
25     False         False     False      False           False   
26     False         False     False      False           False   
27     False         False     False      False           False   
28     False         False     False      False           False   
29     False         False     False      False           False   
30     False         False     False      False           False   
31     False         False     False      False           False   
32     False         False     False      False           False   
33     False         False     False      False           False   
34     False         False     False      False           False   
35     False         False     False      False           False   
36     False         False     False      False           False   
37     False         False     False      False           False   
38     False         False     False      False           False   
39     False         False     False      False           False   
40     False         False     False      False           False   
41     False         False     False      False           False   
42     False         False     False      False           False   
43     False         False     False      False           False   
44     False         False     False      False           False   
45     False         False     False      False           False   
46     False         False     False      False           False   
47     False         False     False      False           False   
48     False         False     False      False           False   
49     False         False     False      False           False   
50     False         False     False      False           False   
51     False         False     False      False           False   
52     False         False     False      False           False   
53     False         False     False      False           False   
54     False         False     False      False           False   
55     False         False     False      False           False   
56     False         False     False      False           False   
57     False         False     False      False           False   
58     False         False     False      False     

In [94]:

newyork_merged = newyork_merged.dropna()

newyork_merged


Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

In [95]:
newyork_merged['Cluster Labels'] = newyork_merged['Cluster Labels'].astype(int)
newyork_merged

Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

Finally, let's visualize the resulting clusters

In [96]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Now lets Examine the Clusters

**Now, we can examine each cluster to determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, we can then assign a name to each cluster.**

In [ ]:
#### Cluster 1

In [104]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 0, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
150        Whitestone       Bubble Tea Shop          Dance Studio   
193        Brookville         Deli / Bodega         Women's Store   
198      New Brighton              Bus Stop         Deli / Bodega   
202       Grymes Hill              Bus Stop               Dog Run   
204       South Beach                 Beach                  Pier   
206  Mariner's Harbor    Italian Restaurant         Deli / Bodega   
224         Park Hill              Bus Stop    Athletics & Sports   
227         Arlington         Deli / Bodega         Grocery Store   
241     Arden Heights              Pharmacy         Deli / Bodega   
256     Randall Manor              Bus Stop            Bagel Shop   
258          Elm Park              Bus Stop         Deli / Bodega   
285       Willowbrook              Bus Stop          Intersection   
305         Fox Hills              Bus Stop            Playground   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
150         Deli / Bodega           Candy Store           Fish Market   
193     Fish & Chips Shop         Event Service           Event Space   
198                  Park         Bowling Alley        Discount Store   
202         Women's Store     Fish & Chips Shop           Event Space   
204         Deli / Bodega              Bus Stop    Athletics & Sports   
206              Bus Stop    Athletics & Sports         Women's Store   
224           Coffee Shop  Gym / Fitness Center                 Hotel   
227        Scenic Lookout            Playground         Women's Store   
241              Bus Stop           Coffee Shop           Pizza Place   
256         Deli / Bodega                  Park         Women's Store   
258    Italian Restaurant           Pizza Place        Cosmetics Shop   
285            Bagel Shop         Deli / Bodega                   Spa   
305           Bus Station        Sandwich Place                   Bar   

          6th Most Common Venue       7th Most Common Venue  \
150                     Exhibit                     Factory   
193                     Exhibit                     Factory   
198                  Playground               Women's Store   
202                     Exhibit                     Factory   
204               Women's Store  Financial or Legal Service   
206           Fish & Chips Shop                 Event Space   
224               Women's Store         Filipino Restaurant   
227                       Field               Event Service   
241               Women's Store         Filipino Restaurant   
256  Financial or Legal Service                 Event Space   
258         American Restaurant              Ice Cream Shop   
285                 Pizza Place               Women's Store   
305               Deli / Bodega                  Food Truck   

          8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
150          Falafel Restaurant                  Farm         Farmers Market  
193          Falafel Restaurant                  Farm         Farmers Market  
198           Fish & Chips Shop               Factory     Falafel Restaurant  
202          Falafel Restaurant                  Farm         Farmers Market  
204                     Exhibit               Factory     Falafel Restaurant  
206                     Exhibit               Factory     Falafel Restaurant  
224                 Event Space               Exhibit                Factory  
227                 Event Space               Exhibit                Factory  
241                 Event Space               Exhibit                Factory  
256                     Exhibit               Factory     Falafel Restaurant  
258                       Field  Fast Food Restaurant         Farmers Market  
285         Filipino Restaurant           Event Space                Exhibit  
305  Financial or Legal Service           Event Space                Exhibit

In [ ]:
#### Cluster 2

In [105]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 1, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood        1st Most Common Venue  \
0                    Wakefield                 Dessert Shop   
1                   Co-op City                  Bus Station   
2                  Eastchester         Caribbean Restaurant   
3                    Fieldston                        Plaza   
4                    Riverdale                         Park   
5                  Kingsbridge                  Pizza Place   
6                  Marble Hill               Sandwich Place   
7                     Woodlawn                Deli / Bodega   
8                      Norwood                         Park   
9               Williamsbridge                    Nightclub   
10                  Baychester                   Donut Shop   
11              Pelham Parkway           Frozen Yogurt Shop   
12                 City Island              Harbor / Marina   
13                Bedford Park                  Pizza Place   
14          University Heights                  Pizza Place   
15              Morris Heights                  IT Services   
16                     Fordham            Mobile Phone Shop   
17                East Tremont                  Pizza Place   
18                  West Farms                  Bus Station   
19                High  Bridge                     Pharmacy   
20                     Melrose                     Pharmacy   
21                  Mott Haven           Spanish Restaurant   
22                 Port Morris             Storage Facility   
23                    Longwood               Sandwich Place   
24                 Hunts Point                   Restaurant   
25                  Morrisania               Discount Store   
26                   Soundview           Chinese Restaurant   
28                 Throgs Neck                Deli / Bodega   
29                Country Club               Sandwich Place   
30                 Parkchester                  Supermarket   
31          Westchester Square         Fast Food Restaurant   
32                    Van Nest                Deli / Bodega   
33                 Morris Park                  Pizza Place   
34                     Belmont           Italian Restaurant   
35              Spuyten Duyvil                         Park   
36             North Riverdale                  Pizza Place   
37                  Pelham Bay           Italian Restaurant   
38               Schuylerville                     Pharmacy   
39              Edgewater Park           Italian Restaurant   
40                 Castle Hill                     Pharmacy   
41                   Olinville         Caribbean Restaurant   
42              Pelham Gardens                  Bus Station   
43                   Concourse                Deli / Bodega   
44                   Unionport                   Donut Shop   
45                    Edenwald                  Supermarket   
46                   Bay Ridge           Italian Restaurant   
47                 Bensonhurst           Italian Restaurant   
48                 Sunset Park    Latin American Restaurant   
49                  Greenpoint                          Bar   
50                   Gravesend                  Pizza Place   
51              Brighton Beach           Russian Restaurant   
52              Sheepshead Bay           Turkish Restaurant   
53           Manhattan Terrace                  Pizza Place   
54                    Flatbush                  Coffee Shop   
55               Crown Heights                  Pizza Place   
56               East Flatbush               Hardware Store   
57                  Kensington                Grocery Store   
58             Windsor Terrace                         Café   
59            Prospect Heights                          Bar   
60                 Brownsville                   Restaurant   
61                Williamsburg                          Bar   
62                    Bushwick                          Bar   
63          Bedford Stuyvesant                  P

In [ ]:
#### Cluster 3

In [99]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 2, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
179     Neponsit                 Beach         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
179     Fish & Chips Shop           Event Space               Exhibit   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
179               Factory    Falafel Restaurant                  Farm   

    9th Most Common Venue 10th Most Common Venue  
179        Farmers Market   Fast Food Restaurant

In [ ]:
#### Cluster 4

In [100]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 3, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue       2nd Most Common Venue  \
27   Clason Point                  Park                    Bus Stop   
76    Mill Island                  Pool  Financial or Legal Service   
192    Somerville                  Park               Women's Store   
203     Todt Hill                  Park               Women's Store   
303     Bayswater                  Park                  Playground   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
27          Moving Target                  Pool         Grocery Store   
76   Ethiopian Restaurant         Event Service           Event Space   
192    English Restaurant         Event Service           Event Space   
203    English Restaurant         Event Service           Event Space   
303         Women's Store   Filipino Restaurant         Event Service   

    6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
27          Boat or Ferry  South American Restaurant         Women's Store   
76                Exhibit                    Factory    Falafel Restaurant   
192               Exhibit                    Factory    Falafel Restaurant   
203               Exhibit                    Factory    Falafel Restaurant   
303           Event Space                    Exhibit               Factory   

          9th Most Common Venue 10th Most Common Venue  
27   Financial or Legal Service                Factory  
76                         Farm         Farmers Market  
192                        Farm         Farmers Market  
203                        Farm         Farmers Market  
303          Falafel Restaurant                   Farm

In [ ]:
#### Cluster 5

In [101]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 4, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
207   Port Ivory                   Bar     Fish & Chips Shop   
212      Oakwood                   Bar            Playground   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
207         Event Service           Event Space               Exhibit   
212           Bus Station                Lawyer         Event Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
207               Factory    Falafel Restaurant                  Farm   
212           Event Space               Exhibit               Factory   

    9th Most Common Venue 10th Most Common Venue  
207        Farmers Market   Fast Food Restaurant  
212    Falafel Restaurant                   Farm